## Storage exercises with mdadm and zfs

### Create volume with 3 drives via mdadm.

Install the package for mdraid on the node:
```bash
apt install mdadm
```
See available drives on your system:
```bash
lsblk
```


```{admonition} output:
    NAME   MAJ:MIN RM   SIZE RO TYPE MOUNTPOINTS
    sda      8:0    0 447.1G  0 disk
    sdb      8:16   0 447.1G  0 disk
    sdc      8:32   0 447.1G  0 disk
    ├─sdc1   8:33   0   512M  0 part /boot/efi
    ├─sdc2   8:34   0 445.7G  0 part /
    └─sdc3   8:35   0   977M  0 part [SWAP]
    sdd      8:48   0 447.1G  0 disk
    sr0     11:0    1   738M  0 rom
```

Pickup unpartitioned drives:
```sda```, ```sdb```, ```sdd``` in this case

Wipe out the superblock on the drives:
```bash
mdadm --zero-superblock --force  /dev/sda /dev/sdb /dev/sdd
```
If the drives were never configured with mdadm:

```{admonition} output:
    mdadm: Unrecognised md component device - /dev/sda
    mdadm: Unrecognised md component device - /dev/sdb
    mdadm: Unrecognised md component device - /dev/sdd
```

Create ```/dev/md0``` raid level #5 with the 3 drives:
```bash
mdadm --create --verbose /dev/md0 --level=5 --raid-devices=3 /dev/sda /dev/sdb /dev/sdd
```
Monitor the status of device ```/dev/md0```:
```bash
mdadm -D /dev/md0
```
or
```bash
cat /proc/mdstat
```

```{admonition} finally the raid volume is created:
    Personalities : [raid6] [raid5] [raid4]
    md0 : active raid5 sdd[3] sdb[1] sda[0]
          937438208 blocks super 1.2 level 5, 512k chunk, algorithm 2 [3/3] [UUU]
          bitmap: 0/4 pages [0KB], 65536KB chunk

    unused devices: <none>
```

### Create and mount exdt4 file system.

Create ext4 file system on ```/dev/md0```:
```bash
mkfs.ext4 /dev/md0
```

Create mounting point:
```bash
mkdir /scratch
```

Mount the file system onto /scratch:
```bash
mount /dev/md0  /scratch
```

verify that the file system is mounted:
```bash
df -h
```

### Destroy the current pool.

```bash
umount /scratch
mdadm --stop /dev/md0
mdadm --remove /dev/md0
```

Clear the drives:
```bash
mdadm --zero-superblock --force /dev/sda /dev/sdb /dev/sdd
```


### ZFS installation

```bash
sudo -s
apt install -y software-properties-common
apt-add-repository contrib
apt update
apt upgrade
```

```bash
apt install zfsutils-linux zfs-dkms zfs-zed
```

### Load module zfs.ko

```bash
modprobe zfs
```

### Create volume.

```bash
lsblk
```

See available drives: /dev/sda, /dev/sdb, /dev/sdd.

Create zpool (volume):
```bash
zpool create -f tank  sda sdb sdd
```


### Create the file system:

```bash
zfs create tank/scratch
```

Check
```bash
df -h
```

It is mounted:
```bash
/tank/scratch
```

### Remove the volume.

```bash
zpool destroy tank
```